In [1]:

import pandas as pd
import numpy as np
import datetime as dt
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import precision_recall_fscore_support
sc = StandardScaler()
import os
import pickle
import fnmatch
from sklearn.metrics import roc_auc_score, accuracy_score, f1_score, recall_score, precision_score

##useful function


def fwd_dates(_dates_list, _key_date):
    # returns a list of dates that are forward from the key_date
    fwd_dates_list = [i for i in _dates_list if i > _key_date]
    return fwd_dates_list

def common_member(a, b): 
      
    a_set = set(a) 
    b_set = set(b) 
      
    # check length  
    if len(a_set.intersection(b_set)) > 0: 
        return(a_set.intersection(b_set))   
    else: 
        return("no common elements") 


def remove_nans(features_tuple, labels, idx=1):
    # not the cleanest but useful
    # function to clean up nans as I seem to use it a lot, so better to have one function
    # combines the features and labels and removes rows with nans across so we dont lose the ordering
    # returns features and labels
    features_df = pd.concat([features_tuple[0], features_tuple[1], features_tuple[2], \
                             features_tuple[3]], axis=1, sort=False)
    labels_only = labels.drop(columns=['ReturnTradedPrice', 'Duration', 'states', 'TradedTime',
                                       'TradedPrice'], axis=1)
    df_concat = pd.concat([features_df, labels_only.iloc[:, 0:idx]], axis=1, sort='False')
    # only using 1st set of labels- but we can re-write this a bit
    df_x_nan = df_concat.dropna()  # dropping all nans
    label_column_loc_ = df_x_nan.shape[1] - 1  # location of labels column in the clean df
    labels_ = df_x_nan.iloc[:, label_column_loc_:label_column_loc_ + 1]  # keep pure labels
    features_ = df_x_nan.drop(df_x_nan.columns[label_column_loc_], axis=1)  # keeping the features only
    return features_, labels_


def prec_recall_report(y_true, y_predict):
    # function to ge the sci-kit learn classification metrics into a pretty DF for csv!
    report = pd.DataFrame(list(precision_recall_fscore_support(y_true, y_predict)),
                          index=['Precision', 'Recall', 'F1-score', 'Support']).T
    # Now add the 'Avg/Total' row
    report.loc['Avg/Total', :] = precision_recall_fscore_support(y_true, y_predict, average='weighted')
    report.loc['Avg/Total', 'Support'] = report['Support'].sum()
    return report


class DataLoader(object):
    def __init__(self, path_main, ticker):
        self.main_path = path_main
        self.ticker = ticker

        self.features_labels_path = os.path.join(self.main_path, 'features_models')
        self.features_path = os.path.join(self.features_labels_path, 'features')
        # collection of per symbol non directional labels
        self.labels_path = os.path.join(self.features_labels_path, 'labels', self.ticker, 'NON_DIRECTIONAL')
        self.symbol_features_path = os.path.join(self.features_labels_path, 'features', self.ticker, 'MODEL_BASED')
        # list of all the model -oos hmm feature dates - each folder is a collection of oos feature dates
        self.hmm_dates_list = os.listdir(self.symbol_features_path)  # each folder are the OOS features from each HMM
        self.compute_date = os.listdir(os.path.join( \
            self.symbol_features_path, \
            os.listdir(self.symbol_features_path)[1]))[1].split("_")[7]

    def ticker_features(self, model_date, date):
        # need to make this a lot more flexible with number of states
        if model_date < date:
            file_name = "_".join(
                (self.ticker, '3', 'states', 'features', 'date:', date, 'now:', self.compute_date, '.pickle'))
            file_loc = os.path.join(self.symbol_features_path, str(model_date), file_name)
            with open(file_loc, 'rb') as handle:
                ticker_features = pickle.load(handle)
        else:
            print('Loading Feature Date which is in-sample. Change your Model Date')
        return ticker_features

    def ticker_labels_csv(self, date):
        file_loc = os.path.join(self.labels_path, str(date) + '.csv')
        ticker_labels = pd.read_csv(file_loc, index_col=0)
        return ticker_labels

    @staticmethod
    def open_pickle_file(path, pickle_file):
        file_loc = os.path.join(path, pickle_file)
        pickle_to_file = pickle.load(open(file_loc, "rb"))
        return pickle_to_file

    @staticmethod
    def get_date_from_file(file_, numb_):
        return os.path.splitext(file_[numb_])[0]

class MarketFeatures(object):
    # a class to be expanded that uses features for base case -market based only-indicators/features
    """"Requires:
    a dataframe that has TradedPrice And Volume columns
    symbol - A stock symbol on which to form a strategy on.
    short_window - Lookback period for short moving average.
    long_window - Lookback period for long moving average.
    """

    def __init__(self, df):
        #         self.ticker = ticker
        self.df = df

    def load_data(self):
        pass

    def ma_spread(self, short_window=5, long_window=20):
        # function that produces the MA spread, which can be used on its own or as an input for MACD
        short_rolling_px = self.df['TradedPrice'].rolling(window=short_window).mean()
        long_rolling_px = self.df['TradedPrice'].rolling(window=long_window).mean()
        px_name = "_".join(('px_indx', str(short_window), str(long_window)))
        self.df[px_name] = long_rolling_px - short_rolling_px
        return self.df

    def ma_spread_duration(self, short_window=5, long_window=20):
        # function that produces the MA spread, which can be used on its own or as an input for MACD
        short_rolling_px = self.df['Duration'].rolling(window=short_window).mean()
        long_rolling_px = self.df['Duration'].rolling(window=long_window).mean()
        dur_name = "_".join(('dur_indx', str(short_window), str(long_window)))
        self.df[dur_name] = long_rolling_px - short_rolling_px
        return self.df

    def obv_calc(self):
        # on balance volume indicator
        self.df['SignedVolume'] = self.df['Volume'] * np.sign(self.df['TradedPrice'].diff()).cumsum()
        self.df['SignedVolume'].iat[1] = 0
        self.df['OBV'] = self.df['SignedVolume']  # .cumsum()
        self.df = self.df.drop(columns=['SignedVolume'])
        return self.df

    def chaikin_mf(self, period=5):
        # Chaikin money flow indicator
        self.df["MF Multiplier"] = (self.df['TradedPrice'] - (self.df['TradedPrice'].expanding(period).min()) \
                                    - (self.df['TradedPrice'].expanding(period).max() \
                                       - self.df['TradedPrice'])) / (
                                           self.df['TradedPrice'].expanding(period).max() - self.df[ \
                                       'TradedPrice'].expanding(period).min())
        self.df["MF Volume"] = self.df['MF Multiplier'] * self.df['Volume']
        self.df['CMF_' + str(period)] = self.df['MF Volume'].sum() / self.df["Volume"].rolling(period).sum()
        self.df = self.df.drop(columns=['MF Multiplier', 'MF Volume'])
        return self.df

In [2]:

# locations

data_dir = os.getenv('FINANCE_DATA')  # main directory referenced in all the code
data_only_drive = '/mnt/usb-Seagate_Expansion_Desk_NA8XEHR6-0:0-part2'  # external date only drive

# this is the central location for all the features/models/predictions
features_models = os.path.join(data_dir,
                               'features_models')
features_models_dod = os.path.join(data_only_drive, 'features_models')
# main path where all the sub-directories are (features, models, labels)

# this is the central location for all the labels
labels = os.path.join(features_models, 'labels')  # label subdirectory
# this is the central location for all the features #feature subdirectory
features = os.path.join(features_models, 'features')

# location to save results
model_save_loc = os.path.join(data_only_drive, 'Data', 'features_models', 'models')

# location where all the models are:

model_save_loc = os.path.join(data_only_drive, 'Data', 'features_models','models')
# from the main directory select all the symbols that are finishing in .L for FTSE
symbols_ftse = [s for s in os.listdir(features) if s.endswith('.L')]

main_path = os.path.join(data_dir, 'features_models')  # main directory

# location to save results
model_loc = os.path.join(data_only_drive, 'Data', 'features_models', 'models')

metrics_loc = os.path.join(data_only_drive, 'Data','features_models','metrics')

features_path = os.path.join(main_path, 'features')  # all the features - same as above -redundant

labels_path = os.path.join(main_path, 'labels')  # all the labels

# same as above- new target directory, where all the models and output is saved
# on the data only drive

model_paths = os.path.join(data_only_drive, 'Data', 'features_models',
                           'models')

# using lambda to make a small function that just takes in the symbol
# and produces the relevant path of all fitted single kernel models
# this path is from the Data Only Drive

def symbol_fitted_models_path(symbol): return os.path.join(model_paths, symbol, 'SINGLE_KERNEL')


# provides a fitted list of above path

def symbol_list_fitted_dates(symbol): return sorted(os.listdir(symbol_fitted_models_path(symbol)))


# fitted model sub-directory- the fitted model is stored in this sub-directory as a pickle

def symbol_fitted_model_date_loc(file_path, model_date_no):
    return os.path.join(file_path, str(symbol_list_fitted_dates(symbol)[model_date_no]))


def symbol_model_date_loc(model_date_path):
    return os.path.join(model_date_path, os.listdir(model_date_path)[0])


def model_pickle_to_svc(model_pickle):

    pickle_to_file = pickle.load(open(model_pickle, "rb"))
    best_estimator = pickle_to_file['SVC'].best_estimator_

    return best_estimator


# test case ##

# symbols to use as a starting point
good_symbols = [
    'RDSa.L', 'PRU.L', 'III.L', 'REL.L', 'CNA.L', 'SHP.L', 'MKS.L',
    'CPI.L', 'ULVR.L', 'ECM.L', 'AV.L', 'GKN.L', 'TSCO.L', 'ITV.L',
    'BARC.L', 'CPG.L', 'AAL.L', 'LGEN.L', 'LAND.L', 'VOD.L', 'HSBA.L',
    'RSA.L', 'DMGOa.L', 'RR.L', 'DGE.L', 'BATS.L', 'MAB.L',
    'KGF.L', 'SPT.L', 'AZN.L'
]



In [3]:
if __name__ == '__main__':


    symbol = good_symbols[1]  # picking PRU as an example

    # test symbol path, which essentially produces the path where all the fitted models are.
    # '/mnt/usb-Seagate_Expansion_Desk_NA8XEHR6-0:0-part2/Data/features_models/models/SPT.L/SINGLE_KERNEL'

    symbol_labels_path = os.path.join(labels_path, symbol, 'NON_DIRECTIONAL')
    
    # specific symbol features list of directories. so this has all the model-based directories of features
    # each date on this list corresponds to an hmm model, and each date-directory contains all the features 
    # constructed out of sample
    
    symbol_features_dates_path = os.path.join(features, symbol, 'MODEL_BASED')
    
    # we construct a list of all the hmm-model-date directories, each containing OOS features
    list_features_dates_dirs = os.listdir(symbol_features_dates_path)
    
    # go into each hmm-model-generated directory and get us the location of that directory
    def oos_date_specific_features_dir(date_dir_no): 
        return os.path.join(symbol_features_dates_path,list_features_dates_dirs[date_dir_no]) #basically 
    
    # this is an example
    oos_feature_file_locations_dict ={}
    oos_labels_file_locations_dict ={}
    for date_idx, date in enumerate(list_features_dates_dirs):

        # create a directory of all the feature locations        
        oos_feature_file_locations_dict[date] = [os.listdir(oos_date_specific_features_dir(date_idx))[loc_idx]
                                              for loc_idx,_ in 
                                               enumerate(os.listdir(oos_date_specific_features_dir(date_idx)))]
    
        # create a directory of all the label locations
        oos_labels_file_locations_dict[date]=[".".join((oos_feature_file_locations_dict[date][idx].split("_")[5],"csv"))
                                             for idx,_ in enumerate(oos_feature_file_locations_dict[date])]
        
        # go through all the keys and basically get the out of sample features and labels
        keys= oos_feature_file_locations_dict.keys()
        

    
    
    

In [4]:
datacls = DataLoader(path_main=data_dir, ticker=symbol)  # test symbol -create class
symbol_compute_date = datacls.compute_date
from collections import defaultdict
all_symbols_d = defaultdict(dict)
symbol_model_dates = dict()

In [43]:
print symbol
test_path = symbol_fitted_models_path(symbol=symbol)

# now lets take all the model directories and locations##
model_directories = [symbol_fitted_model_date_loc(test_path, idx) for idx, date in enumerate(os.listdir(test_path))]
models_locations = [os.path.join(model_directories[dir_idx], os.listdir(model_directories[dir_idx])[0]) for
                    dir_idx, model_dir in enumerate(model_directories)]
for model_idx, model_loc in enumerate(models_locations):
    model_date = model_loc.split("_")[6]
    print ('model date is:',model_date)
    model_pickle = model_loc

    print model_pickle
    pickle_to_file = pickle.load(open(model_pickle, "rb")) #load your model

    best_estimator = pickle_to_file['SVC'].best_estimator_

    print('Your symbol is:', symbol, 'and the model date is:' ,model_date)
    fwd_dates_list = [i for i in keys if i > model_date]
    # set up the dictionary for metrics #
    M = len(fwd_dates_list)
    T = 1
    T_2 = 4
    fitted_models_results = {
            'accuracy': np.empty((M,T)),
            'recall': np.empty((M,T)),
            'F1-score': np.empty((M,T)),
            'precision_recall_fscore_support': np.empty((M, T_2))
        }
    for key in fwd_dates_list:
        listA=oos_feature_file_locations_dict[key] # list of out of sample features
        listB=oos_labels_file_locations_dict[key] # list of out of sample labels
        for a, b in zip(listA, listB):
            if fwd_date > model_date:
                fwd_date=b.split(".")[0]
                features_date= a.split("_")[5]
                print('model date', model_date)
                print('features_date', features_date)
            else:
                print('tiny problem, model date is not behind!')
#             exists=os.path.isfile(os.path.join(symbol_features_dates_path,key,a))            
#             if exists:
#                 print('###-computing-###')
#                 features_tuple=pickle.load(open(os.path.join(symbol_features_dates_path,key,a), "rb"))
#                 market_data_oos= pd.read_csv(os.path.join(symbol_labels_path, b),index_col=0)
# #                 features_df = pd.concat([features_tuple[0], features_tuple[1],
# #                                      features_tuple[2], features_tuple[3]], axis=1, sort=False)
# #                 df_w_market_features = MarketFeatures(df=MarketFeatures(\
# #                     df=MarketFeatures(
#                         df=MarketFeatures(df=market_data_oos).obv_calc()).chaikin_mf()).ma_spread()).ma_spread_duration()

#                 df_concat = pd.concat([features_df, df_w_market_features], axis=1, sort='False').dropna()

#                 label_name = str(df_concat.columns[df_concat.columns.str.contains(pat='label')].values[0])

#                 df_final = df_concat.drop(columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', \
#                                                    'Volume', label_name])
#                 if len(df_final)> 5:
#                     X = MinMaxScaler().fit_transform(df_final)

#                     y_labels = df_concat[df_concat.columns[df_concat.columns.str.contains(pat='label')]].iloc[:, 0]
#                     y_predict = best_estimator.predict(X)
#                     print accuracy_score(y_labels, y_predict)
#                 else:
#                     print('skipping...')

#     #                 results_loc = str(os.path.join(metrics_loc, "_".join((symbol,model_date,"results_metrics.pickle"))))
#     #                 fitted_models_results['accuracy'][fwd_date, :] = accuracy_score(y_labels, y_predict)
#     #                 fitted_models_results['recall'][fwd_date, :] = recall_score(y_true=y_labels, y_pred=y_predict)
#     #                 fitted_models_results['F1-score'][fwd_date, :] =f1_score(y_true= y_labels, y_pred=y_predict)
#     #                 fitted_models_results['precision_recall_fscore_support'][fwd_idx, :] = precision_recall_fscore_support(y_true=  y_labels, y_pred=y_predict, average='micro')

#     #                 with open(results_loc, 'wb') as f:
#     #                     pickle.dump(fitted_models_results, f)
#             else:
#                 print ('problem')

#             #             features_tuple = pickle.load(open(os.path.join(symbol_features_dates_path,a), "rb"))

PRU.L
('model date is:', '20170117')
/mnt/usb-Seagate_Expansion_Desk_NA8XEHR6-0:0-part2/Data/features_models/models/PRU.L/SINGLE_KERNEL/20170117/PRU.L_20170117_label_PrMov__window_5__thres_arbitrary__0.1_clf_fitted_.pickle
('Your symbol is:', 'PRU.L', 'and the model date is:', '20170117')
('model date', '20170117')
('features_date', '20170704')
('model date', '20170117')
('features_date', '20180409')
('model date', '20170117')
('features_date', '20180221')
('model date', '20170117')
('features_date', '20170705')
('model date', '20170117')
('features_date', '20170718')
('model date', '20170117')
('features_date', '20180416')
('model date', '20170117')
('features_date', '20170802')
('model date', '20170117')
('features_date', '20180212')
('model date', '20170117')
('features_date', '20170727')
('model date', '20170117')
('features_date', '20180410')
('model date', '20170117')
('features_date', '20170726')
('model date', '20170117')
('features_date', '20180208')
('model date', '20170117')

('features_date', '20170818')
('model date', '20170117')
('features_date', '20180219')
('model date', '20170117')
('features_date', '20180220')
('model date', '20170117')
('features_date', '20170808')
('model date', '20170117')
('features_date', '20170803')
('model date', '20170117')
('features_date', '20180406')
('model date', '20170117')
('features_date', '20180404')
('model date', '20170117')
('features_date', '20180409')
('model date', '20170117')
('features_date', '20180221')
('model date', '20170117')
('features_date', '20180416')
('model date', '20170117')
('features_date', '20180410')
('model date', '20170117')
('features_date', '20180226')
('model date', '20170117')
('features_date', '20180420')
('model date', '20170117')
('features_date', '20180418')
('model date', '20170117')
('features_date', '20180412')
('model date', '20170117')
('features_date', '20180223')
('model date', '20170117')
('features_date', '20180222')
('model date', '20170117')
('features_date', '20180228')
(

('features_date', '20180417')
('model date', '20170117')
('features_date', '20180213')
('model date', '20170117')
('features_date', '20180411')
('model date', '20170117')
('features_date', '20180403')
('model date', '20170117')
('features_date', '20180227')
('model date', '20170117')
('features_date', '20180214')
('model date', '20170117')
('features_date', '20180405')
('model date', '20170117')
('features_date', '20180419')
('model date', '20170117')
('features_date', '20180413')
('model date', '20170117')
('features_date', '20180216')
('model date', '20170117')
('features_date', '20180219')
('model date', '20170117')
('features_date', '20180220')
('model date', '20170117')
('features_date', '20180406')
('model date', '20170117')
('features_date', '20180404')
('model date', '20170117')
('features_date', '20180409')
('model date', '20170117')
('features_date', '20180221')
('model date', '20170117')
('features_date', '20180416')
('model date', '20170117')
('features_date', '20180212')
(

('features_date', '20170822')
('model date', '20170117')
('features_date', '20170825')
('model date', '20170117')
('features_date', '20180209')
('model date', '20170117')
('features_date', '20170731')
('model date', '20170117')
('features_date', '20170131')
('model date', '20170117')
('features_date', '20170801')
('model date', '20170117')
('features_date', '20170809')
('model date', '20170117')
('features_date', '20170811')
('model date', '20170117')
('features_date', '20180413')
('model date', '20170117')
('features_date', '20180216')
('model date', '20170117')
('features_date', '20170818')
('model date', '20170117')
('features_date', '20180219')
('model date', '20170117')
('features_date', '20170714')
('model date', '20170117')
('features_date', '20170713')
('model date', '20170117')
('features_date', '20180220')
('model date', '20170117')
('features_date', '20170719')
('model date', '20170117')
('features_date', '20170725')
('model date', '20170117')
('features_date', '20170808')
(

('model date', '20170118')
('features_date', '20180406')
('model date', '20170118')
('features_date', '20180404')
('model date', '20170118')
('features_date', '20180409')
('model date', '20170118')
('features_date', '20180221')
('model date', '20170118')
('features_date', '20180416')
('model date', '20170118')
('features_date', '20180410')
('model date', '20170118')
('features_date', '20180226')
('model date', '20170118')
('features_date', '20180420')
('model date', '20170118')
('features_date', '20180418')
('model date', '20170118')
('features_date', '20180412')
('model date', '20170118')
('features_date', '20180223')
('model date', '20170118')
('features_date', '20180222')
('model date', '20170118')
('features_date', '20180228')
('model date', '20170118')
('features_date', '20180417')
('model date', '20170118')
('features_date', '20180411')
('model date', '20170118')
('features_date', '20180403')
('model date', '20170118')
('features_date', '20180227')
('model date', '20170118')
('fe

...

('features_date', '20180409')
('model date', '20180209')
('features_date', '20180416')
('model date', '20180209')
('features_date', '20180410')
('model date', '20180209')
('features_date', '20180420')
('model date', '20180209')
('features_date', '20180418')
('model date', '20180209')
('features_date', '20180412')
('model date', '20180209')
('features_date', '20180417')
('model date', '20180209')
('features_date', '20180411')
('model date', '20180209')
('features_date', '20180419')
('model date', '20180209')
('features_date', '20180413')
('model date', '20180209')
('features_date', '20180406')
('model date', '20180209')
('features_date', '20180409')
('model date', '20180209')
('features_date', '20180416')
('model date', '20180209')
('features_date', '20180410')
('model date', '20180209')
('features_date', '20180420')
('model date', '20180209')
('features_date', '20180418')
('model date', '20180209')
('features_date', '20180412')
('model date', '20180209')
('features_date', '20180417')
(

('Your symbol is:', 'PRU.L', 'and the model date is:', '20180214')
('model date', '20180214')
('features_date', '20180409')
('model date', '20180214')
('features_date', '20180221')
('model date', '20180214')
('features_date', '20180416')
('model date', '20180214')
('features_date', '20180410')
('model date', '20180214')
('features_date', '20180226')
('model date', '20180214')
('features_date', '20180420')
('model date', '20180214')
('features_date', '20180418')
('model date', '20180214')
('features_date', '20180412')
('model date', '20180214')
('features_date', '20180223')
('model date', '20180214')
('features_date', '20180222')
('model date', '20180214')
('features_date', '20180228')
('model date', '20180214')
('features_date', '20180417')
('model date', '20180214')
('features_date', '20180411')
('model date', '20180214')
('features_date', '20180403')
('model date', '20180214')
('features_date', '20180227')
('model date', '20180214')
('features_date', '20180405')
('model date', '20180

('features_date', '20180413')
('model date', '20180216')
('features_date', '20180409')
('model date', '20180216')
('features_date', '20180416')
('model date', '20180216')
('features_date', '20180410')
('model date', '20180216')
('features_date', '20180420')
('model date', '20180216')
('features_date', '20180418')
('model date', '20180216')
('features_date', '20180412')
('model date', '20180216')
('features_date', '20180417')
('model date', '20180216')
('features_date', '20180411')
('model date', '20180216')
('features_date', '20180405')
('model date', '20180216')
('features_date', '20180419')
('model date', '20180216')
('features_date', '20180413')
('model date', '20180216')
('features_date', '20180406')
('model date', '20180216')
('features_date', '20180404')
('model date is:', '20180219')
/mnt/usb-Seagate_Expansion_Desk_NA8XEHR6-0:0-part2/Data/features_models/models/PRU.L/SINGLE_KERNEL/20180219/PRU.L_20180219_label_PrMov__window_5__thres_arbitrary__0.1_clf_fitted_.pickle
('Your symbo

('model date', '20180222')
('features_date', '20180420')
('model date', '20180222')
('features_date', '20180418')
('model date', '20180222')
('features_date', '20180412')
('model date', '20180222')
('features_date', '20180417')
('model date', '20180222')
('features_date', '20180411')
('model date', '20180222')
('features_date', '20180419')
('model date', '20180222')
('features_date', '20180413')
('model date', '20180222')
('features_date', '20180409')
('model date', '20180222')
('features_date', '20180416')
('model date', '20180222')
('features_date', '20180410')
('model date', '20180222')
('features_date', '20180420')
('model date', '20180222')
('features_date', '20180418')
('model date', '20180222')
('features_date', '20180412')
('model date', '20180222')
('features_date', '20180417')
('model date', '20180222')
('features_date', '20180411')
('model date', '20180222')
('features_date', '20180405')
('model date', '20180222')
('features_date', '20180419')
('model date', '20180222')
('fe

('Your symbol is:', 'PRU.L', 'and the model date is:', '20180403')
('model date', '20180403')
('features_date', '20180420')
('model date', '20180403')
('features_date', '20180419')
('model date', '20180403')
('features_date', '20180420')
('model date', '20180403')
('features_date', '20180416')
('model date', '20180403')
('features_date', '20180420')
('model date', '20180403')
('features_date', '20180418')
('model date', '20180403')
('features_date', '20180417')
('model date', '20180403')
('features_date', '20180419')
('model date', '20180403')
('features_date', '20180413')
('model date', '20180403')
('features_date', '20180416')
('model date', '20180403')
('features_date', '20180420')
('model date', '20180403')
('features_date', '20180418')
('model date', '20180403')
('features_date', '20180417')
('model date', '20180403')
('features_date', '20180419')
('model date', '20180403')
('features_date', '20180416')
('model date', '20180403')
('features_date', '20180420')
('model date', '20180

In [38]:
os.path.join(symbol_features_dates_path,key,a)

'/media/ak/WorkDrive/Data/features_models/features/PRU.L/MODEL_BASED/20180419/PRU.L_3_states_features_date:_20180420_now:_20181229_.pickle'

In [41]:
fwd_date

'20180420'

In [ ]:
    import os
    exists = os.path.isfile('/path/to/file')
    if exists:
        # Store configuration file values
    else:
        # Keep presets

In [ ]:
fwd_dates_list

In [ ]:
fwd_dates_list